# Twitter Extraction

In [16]:
%matplotlib inline
from bs4 import BeautifulSoup
# import urllib2
from urllib.request import urlopen
import urllib
import json
import csv
import time
import pickle
import pandas as pd
import numpy as np
import scipy as sp
import matplotlib as mpl
import matplotlib.cm as cm
import matplotlib.pyplot as plt
import pandas as pd
pd.set_option('display.width', 500)
pd.set_option('display.max_columns', 100)
pd.set_option('display.notebook_repr_html', True)
import seaborn as sns
import sys
import os
import time
sns.set_style("whitegrid")
sns.set_context("poster")

In [17]:
def load_obj(name):
    with open(name + '.pkl', 'rb') as f:
        return pickle.load(f)
    
def merge_d(x, y):
    z = x.copy()
    z.update(y)
    return z

def flatten_data(t_data):
    t_data_f= {}
    for key in t_data.keys():
        for key2 in t_data[key].keys():
            t_data_f[key + '_' + key2] = t_data[key][key2]
    return t_data_f

twit_data = flatten_data(load_obj('twit_data1'))
t_data_num = 1

def backup(obj, t_data_num = t_data_num):
    name = "t_df" + str(t_data_num)
    with open(name + '.pkl', 'wb') as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)

In [18]:
company_l = []
series_l = []
text_l = [] 
time_l = []
retweets_l = []
likes_l = []
name_l = []
href_l = []
errors = []
max_ind = len(twit_data.keys())
start = time.time()

for i in range(max_ind):    
    
    # Timing code and backup code
    if i % 50 == 0:
        mins = (time.time() - start) / 60
        print('Percent progress ' + str(100.0 * i / max_ind) + ' running for ' + str(mins) + ' mins')        
        data_backup = {'Company': company_l, 'Series': series_l, 'Text': text_l, 'Time':time_l, 'Retweets':retweets_l, 'Likes':likes_l, 'Name':name_l, 'Href':href_l}
        backup(data_backup)
    
    # Finding the series of the data
    company_series = twit_data.keys()[i]
    ind = company_series[:company_series.rfind("_")].rfind("_")
    company = company_series[:ind]
    series = company_series[ind:]
    backup({'Company': company_l, 'Series': series_l, 'Text': text_l, 'Time':time_l, 'Retweets':retweets_l, 'Likes':likes_l, 'Name':name_l, 'Href':href_l})
    
    
    # Loop through each copmany and series pair and extract relevant information
    for tweet in twit_data[company_series]:
        try:
            # Searching
            soup = BeautifulSoup(tweet, 'lxml')
            actions = soup.find_all('div', class_='ProfileTweet-actionCountList')[0]
            text = soup.find_all('p', class_ = 'TweetTextSize')[0].text
            times = soup.find_all('a', class_ = 'tweet-timestamp')[0].text
            retweets = actions.find_all('span', class_='ProfileTweet-actionCount')[0].text.strip()
            likes = actions.find_all('span', class_='ProfileTweet-actionCount')[1].text.strip()
            name = soup.find_all('strong', class_='fullname')[0].text
            href = soup.find_all('a', class_='account-group')[0]['href']
            
            # Storing
            company_l.append(company)
            series_l.append(series)
            text_l.append(text)
            time_l.append(times)
            retweets_l.append(retweets)
            likes_l.append(likes)
            name_l.append(name)
            href_l.append(href)
            
        # Only listen for keyboard exceptions
        except KeyboardInterrupt:
            try:
                sys.exit(0)
            except SystemExit:
                os._exit(0) 
        except:
            errors.append(tweet)

In [19]:
tweets = pd.read_csv("tweets.csv", encoding="utf-8", engine="c")
tweets_translated = pd.read_csv("translatedTweets.csv", encoding="utf-8", engine="c")
tweets_translated.head()

C:\Users\MY PC\AppData\Local\Temp\ipykernel_5472\4292983939.py:2: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  tweets_translated = pd.read_csv("translatedTweets.csv", encoding="utf-8", engine="c")


Unnamed: 0.1 Unnamed: 0    Company           Href    Likes              Name    Retweets     Series                                               Text       Time
0           0.0          0  Occipital  /yehyehgluglu  0 likes        Maria Melo  0 retweets  _Series_A  @rubaums2 mira in the occipital and frontal to...  14-Jul-11
1           1.0          2  Occipital  /ArturoMisifu  0 likes    Arturo Quijano  0 retweets  _Series_A  at the height of the occipital head - hurts if...  14-Jul-11
2           2.0          5  Occipital     /victorcab  0 likes  Victor Caballero  0 retweets  _Series_A  Tripod – Timer for 360 Views – iPhone? : http:...  14-Jul-11
3           3.0          7  Occipital   /electroniko  0 likes    MIGUEL NEGRETE  0 retweets  _Series_A  Neurona, glia, axon myelin, parietal, temporal...  14-Jul-11
4           4.0          8  Occipital    /nomina_bot  0 likes              体野ミナ  0 retweets  _Series_A  Greater occipital nerve:nervus occipitalis maj...  13-Jul-11

In [20]:
tweets

Company            Href    Likes            Name    Retweets     Series                                               Text         Time
0        Occipital   /yehyehgluglu  0 likes      Maria Melo  0 retweets  _Series_A  @rubaums2 mira no frontal  até o occipital e f...  14 Jul 2011
1        Occipital      /occipital  0 likes       Occipital   1 retweet  _Series_A  Cats out of the bag, we're excited! RT @savvys...  14 Jul 2011
2        Occipital   /ArturoMisifu  0 likes  Arturo Quijano  0 retweets  _Series_A  me duele la cabeza a la altura del occipital -...  14 Jul 2011
3        Occipital        /ortidog  0 likes      Paul White  0 retweets  _Series_A  No matter what happens, I always have the Occi...  14 Jul 2011
4        Occipital   /durlancastro  0 likes   Durlan Castro  0 retweets  _Series_A  Headaches are mostly caused by adhesions in th...  14 Jul 2011
...            ...             ...      ...             ...         ...        ...                                                ...          ...
387842  OvaScience     /OvaScience  0 likes      OvaScience   1 retweet  _Series_D  OvaScience to present today:  http://www.marke...  11 Sep 2012
387843  OvaScience  /BioPharmaJosh  0 likes     Josh Berlin  0 retweets  _Series_D  Pink Sheet Daily: Financings Of The Fortnight ...   7 Sep 2012
387844  OvaScience     /OvaScience  0 likes      OvaScience   1 retweet  _Series_D  OvaScience to Present at Upcoming 2012 Investo...   7 Sep 2012
387845  OvaScience       /cynthfox  0 likes        cynthfox  0 retweets  _Series_D  OvaScience to Present at the Stifel Nicolaus 2...   6 Sep 2012
387846  OvaScience    /News_Pharma  0 likes     Pharma News  0 retweets  _Series_D  Intercept and OvaScience file for IPOs to prog...   5 Sep 2012

[387847 rows x 8 columns]

In [21]:
# Calculating relative dates based off of dates like Apr, 5 2015. We can use this later
# for calculating average number of tweets per day.
months = {'Jan':1, 'Feb':2, 'Mar':3, 'Apr':4, 'May':5, 'Jun':6, 'Jul':7, 'Aug':8, 'Sep':9, 'Oct':10, 'Nov':11, 'Dec':12}



In [22]:
time_sub = []
for row in tweets.iterrows():
    print(row[1]['Time'])
    if type(row[1]['Time']) != str():
        time_sub.append(0)
    elif len(row[1]['Time'].split(' ')) == 3:
        if row[1]['Time'].split(' ')[1] in months.keys():        
            time_sub.append(int(row[1]['Time'].split(' ')[2]) * 365 + months[row[1]['Time'].split(' ')[1]] * 30 + int(row[1]['Time'].split(' ')[0]))
        else:
            time_sub.append(0)
    else:
        time_sub.append(0)
        


14 Jul 2011
14 Jul 2011
14 Jul 2011
14 Jul 2011
14 Jul 2011
14 Jul 2011
14 Jul 2011
14 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
13 Jul 2011
12 Jul 2011
12 Jul 2011
12 Jul 2011
12 Jul 2011
12 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
11 Jul 2011
10 Jul 2011
10 Jul 2011
10 Jul 2011
10 Jul 2011
9 Jul 2011
9 Jul 2011
9 Jul 2011
9 Jul 2011
9 Jul 2011
9 Jul 2011
9 Jul 2011
9 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
8 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 Jul 2011
7 

22 Mar 2012
21 Mar 2012
20 Mar 2012
20 Mar 2012
20 Mar 2012
19 Mar 2012
6 Mar 2012
1 Feb 2012
10 Jan 2012
5 Dec 2011
1 Dec 2011
10 Nov 2011
10 Nov 2011
4 Nov 2011
14 Oct 2011
1 Oct 2011
30 Sep 2011
27 Sep 2011
8 Sep 2011
6 Sep 2011
1 Sep 2011
31 Aug 2011
18 Aug 2011
12 Aug 2011
25 Jul 2011
25 Jul 2011
21 Jul 2011
22 Jun 2011
16 Jun 2011
9 Jun 2011
3 Jun 2011
18 May 2011
18 May 2011
17 May 2011
16 May 2011
16 May 2011
8 Mar 2011
7 Mar 2011
24 Feb 2011
6 Jan 2011
4 Jan 2011
22 Dec 2010
6 Dec 2010
29 Nov 2010
29 Nov 2010
15 Nov 2010
23 Sep 2010
17 Aug 2010
16 Aug 2010
5 Aug 2010
4 Aug 2010
3 Aug 2010
29 Jun 2010
22 Jun 2010
21 Jun 2010
21 Jun 2010
16 Jun 2010
20 May 2010
27 Apr 2010
9 Apr 2010
18 Mar 2010
10 Mar 2010
24 Feb 2010
18 Feb 2010
10 Feb 2010
11 Jan 2010
8 Jan 2010
1 Dec 2009
5 Nov 2009
28 Oct 2009
16 Oct 2009
1 Sep 2009
21 Aug 2009
29 Nov 2012
26 Nov 2012
12 Sep 2012
11 Sep 2012
11 Sep 2012
24 Jul 2012
23 Jul 2012
8 Mar 2012
9 Feb 2012
9 Feb 2012
4 Feb 2012
3 Feb 2012
31 Jan 20

25 Sep 2012
25 Sep 2012
25 Sep 2012
25 Sep 2012
24 Sep 2012
24 Sep 2012
24 Sep 2012
23 Sep 2012
21 Sep 2012
21 Sep 2012
21 Sep 2012
21 Sep 2012
20 Sep 2012
20 Sep 2012
20 Sep 2012
20 Sep 2012
19 Sep 2012
19 Sep 2012
19 Sep 2012
19 Sep 2012
18 Sep 2012
18 Sep 2012
17 Sep 2012
17 Sep 2012
17 Sep 2012
17 Sep 2012
16 Sep 2012
15 Sep 2012
15 Sep 2012
14 Sep 2012
14 Sep 2012
14 Sep 2012
14 Sep 2012
14 Sep 2012
13 Sep 2012
13 Sep 2012
13 Sep 2012
13 Sep 2012
13 Sep 2012
13 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
12 Sep 2012
11 Sep 2012
10 Sep 2012
10 Sep 2012
10 Sep 2012
10 Sep 2012
10 Sep 2012
9 Sep 2012
9 Sep 2012
9 Sep 2012
9 Sep 2012
9 Sep 2012
9 Sep 2012
8 Sep 2012
8 Sep 2012
8 Sep 2012
8 Sep 2012
8 Sep 2012
7 Sep 2012
7 Sep 2012
6 Sep 2012
6 Sep 2012
6 Sep 2012
6 Sep 2012
5 Sep 2012
5 Sep 2012
5 Sep 2012
5 Sep 2012
2 Sep 2012
2 Sep 2012
2 Sep 2012
1 Sep 2012
1 Sep 2012
1 Sep 2012
1 Sep 2012
1 Sep 2012
31 Aug 20

26 Sep 2013
26 Sep 2013
26 Sep 2013
26 Sep 2013
26 Sep 2013
26 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
25 Sep 2013
14 Oct 2009
14 Oct 2009
14 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
13 Oct 2009
12 Oct 2009
12 Oct 2009
12 Oct 2009
12 Oct 2009
12 Oct 2009
12 Oct 2009
12 Oct 2009
11 Oct 2009
11 Oct 2009
11 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
10 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
9 Oct 2009
8 Oct 2009
8 Oct 2009
8 Oct 2009
8 Oct 2009
8 Oct 2009
8 Oct 2

5 Dec 2010
5 Dec 2010
10 Nov 2010
8 Nov 2010
1 Nov 2010
26 Oct 2010
26 Oct 2010
10 Oct 2010
8 Oct 2010
7 Oct 2010
3 Oct 2010
3 Oct 2010
1 Oct 2010
26 Sep 2010
16 Sep 2010
15 Sep 2010
12 Sep 2010
12 Sep 2010
24 Aug 2010
24 Aug 2010
16 Aug 2010
8 Aug 2010
5 Aug 2010
26 Jul 2010
19 Jul 2010
19 Jul 2010
9 Jul 2010
8 Jul 2010
7 Jul 2010
7 Jul 2010
30 Jun 2010
30 Jun 2010
29 Jun 2010
27 Jun 2010
24 Jun 2010
22 Jun 2010
26 May 2010
25 May 2010
25 May 2010
21 May 2010
20 May 2010
18 May 2010
17 May 2010
12 May 2010
8 May 2010
28 Apr 2010
14 Apr 2010
13 Apr 2010
1 Apr 2010
1 Apr 2010
19 Mar 2010
17 Mar 2010
9 Mar 2010
24 Feb 2010
16 Feb 2010
13 Feb 2010
29 Jan 2010
27 Jan 2010
24 Jan 2010
8 Jan 2010
3 Jan 2010
2 Jan 2010
29 Dec 2009
29 Dec 2009
28 Dec 2009
25 Dec 2009
23 Dec 2009
23 Dec 2009
8 Dec 2009
2 Dec 2009
30 Nov 2009
22 Nov 2009
22 Nov 2009
19 Nov 2009
19 Nov 2009
18 Nov 2009
18 Nov 2009
17 Nov 2009
14 Nov 2009
13 Nov 2009
6 Nov 2009
26 Oct 2009
21 Oct 2009
6 Oct 2009
1 Oct 2009
24 Sep 

...

21 Jun 2009
3 Jun 2009
2 Jun 2009
2 Jun 2009
21 May 2009
21 May 2009
21 May 2009
12 May 2009
12 May 2009
8 May 2009
29 Apr 2009
23 Apr 2009
23 Apr 2009
14 Apr 2009
9 Apr 2009
6 Apr 2009
27 Mar 2009
25 Mar 2009
5 Feb 2009
2 Feb 2009
8 Jan 2009
16 Oct 2008
9 Sep 2008
5 Aug 2008
31 Jul 2008
23 Apr 2008
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
14 Nov 2010
13 Nov 2010
13 Nov 2010
13 Nov 2010
13 Nov 2010
13 Nov 2010
13 Nov 2010
13 Nov 2010
13 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
12 Nov 2010
11 Nov 2010
11 Nov 2010
11 

14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
14 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 Mar 2014
13 M

7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
7 Jul 2014
6 Jul 2014
6 Jul 2014
6 Jul 2014
6 Jul 2014
5 Jul 2014
5 Jul 2014
5 Jul 2014
5 Jul 2014
5 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
4 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
3 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
2 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
1 Jul 2014
30 Jun 2014
30 Jun 2014
30 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
29 Jun 2014
28 Jun 2014
28 Jun 2014
28 Jun 2014
28 Jun 2014
28 Jun 2014
28 Jun 20

13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
13 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 Aug 2011
12 A

26 Mar 2009
18 Jan 2009
28 Apr 2009
28 Apr 2009
12 May 2013
11 May 2013
10 May 2013
9 May 2013
9 May 2013
5 May 2013
4 May 2013
3 May 2013
2 May 2013
2 May 2013
1 May 2013
30 Apr 2013
28 Apr 2013
27 Apr 2013
27 Apr 2013
27 Apr 2013
26 Apr 2013
26 Apr 2013
26 Apr 2013
26 Apr 2013
26 Apr 2013
25 Apr 2013
25 Apr 2013
24 Apr 2013
24 Apr 2013
24 Apr 2013
23 Apr 2013
23 Apr 2013
23 Apr 2013
23 Apr 2013
23 Apr 2013
23 Apr 2013
22 Apr 2013
22 Apr 2013
22 Apr 2013
22 Apr 2013
21 Apr 2013
20 Apr 2013
20 Apr 2013
19 Apr 2013
19 Apr 2013
19 Apr 2013
19 Apr 2013
18 Apr 2013
17 Apr 2013
16 Apr 2013
16 Apr 2013
16 Apr 2013
15 Apr 2013
10 Apr 2013
10 Apr 2013
10 Apr 2013
8 Apr 2013
4 Apr 2013
4 Apr 2013
3 Apr 2013
3 Apr 2013
2 Apr 2013
2 Apr 2013
2 Apr 2013
2 Apr 2013
2 Apr 2013
1 Apr 2013
1 Apr 2013
1 Apr 2013
1 Apr 2013
1 Apr 2013
1 Apr 2013
31 Mar 2013
31 Mar 2013
30 Mar 2013
30 Mar 2013
30 Mar 2013
29 Mar 2013
28 Mar 2013
28 Mar 2013
27 Mar 2013
27 Mar 2013
27 Mar 2013
27 Mar 2013
27 Mar 2013
27 M

In [23]:
time_sub = []
for row in tweets.iterrows():
    if pd.notna(row[1]['Time']):
        if row[1]['Time'].split(' ')[1] in months.keys():
            time_sub.append(int(row[1]['Time'].split(' ')[2]) * 365 + months[row[1]['Time'].split(' ')[1]] * 30 + int(row[1]['Time'].split(' ')[0]))
        else:
            time_sub.append(0)
    else:
        time_sub.append(0)

In [24]:
time_sub

[734239,
 734239,
 734239,
 734239,
 734239,
 734239,
 734239,
 734239,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734238,
 734237,
 734237,
 734237,
 734237,
 734237,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734236,
 734235,
 734235,
 734235,
 734235,
 734234,
 734234,
 734234,
 734234,
 734234,
 734234,
 734234,
 734234,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734233,
 734232,
 734232,
 734232,
 734232,
 734232,
 734232,
 734232,
 734232,
 734232,
 734232,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734231,
 734230,
 734230,
 734230,
 734230,
 734230,
 734230,
 734230,
 734230,
 734230,
 734230,
 734230,
 

In [25]:
tweets['Date_Num'] = time_sub
tweets = tweets[tweets['Date_Num'] != 0]
print(tweets)



           Company            Href    Likes            Name    Retweets     Series                                               Text         Time  Date_Num
0        Occipital   /yehyehgluglu  0 likes      Maria Melo  0 retweets  _Series_A  @rubaums2 mira no frontal  até o occipital e f...  14 Jul 2011    734239
1        Occipital      /occipital  0 likes       Occipital   1 retweet  _Series_A  Cats out of the bag, we're excited! RT @savvys...  14 Jul 2011    734239
2        Occipital   /ArturoMisifu  0 likes  Arturo Quijano  0 retweets  _Series_A  me duele la cabeza a la altura del occipital -...  14 Jul 2011    734239
3        Occipital        /ortidog  0 likes      Paul White  0 retweets  _Series_A  No matter what happens, I always have the Occi...  14 Jul 2011    734239
4        Occipital   /durlancastro  0 likes   Durlan Castro  0 retweets  _Series_A  Headaches are mostly caused by adhesions in th...  14 Jul 2011    734239
...            ...             ...      ...             ..

In [26]:
valid_data = []

for val in zip(list((tweets.groupby(['Company', 'Series']).size() > 150).index), list((tweets.groupby(['Company', 'Series']).size() > 150).values)):    
    print(val[1])
    if val[1]:
        print(val[0])
        valid_data.append(val[0])
        


True
('140Proof', '_Series_B')
True
('1stdibs', '_Series_C')
False
False
False
False
False
True
('2tor', '_Series_C')
False
True
('365Scores', '_Series_B')
True
('36Kr', '_Series_C')
True
('3Drobotics', '_Series_A')
False
False
False
False
False
False
False
False
False
True
('6fusion', '_Series_B')
True
('6sense', '_Series_A')
False
False
True
('8Securities', '_Series_A')
False
False
False
False
False
False
False
False
True
('AHAlife', '_Series_B')
False
False
True
('AbilTo', '_Series_A')
True
('AbilTo', '_Series_B')
True
('Abiquo', '_Series_A')
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
False
True
('Achievers', '_Series_A')
True
('Achievers', '_Series_C')
True
('ActOnSoftware', '_Series_B')
True
('ActOnSoftware', '_Series_C')
True
('ActOnSoftware', '_Series_D')
False
True
('ActonSoftware', '_Series_B')
True
('ActonSoftware', '_Series_C')
True
('ActonSoftware', '_Series_D')
True
('Acumatica', '_Series_C')
False
False
False
False
False
Fals

In [27]:
# We also only filter the tweets based off of whether or not there was 150 tweets in the past
valid_tweets = []
for valid_pair in valid_data:
    company = valid_pair[0]
    series = valid_pair[1]
    match_company = tweets[tweets['Company'] == company]
    valid_tweets.append(match_company[match_company['Series'] == series])

In [28]:
print(valid_data)

[('140Proof', '_Series_B'), ('1stdibs', '_Series_C'), ('2tor', '_Series_C'), ('365Scores', '_Series_B'), ('36Kr', '_Series_C'), ('3Drobotics', '_Series_A'), ('6fusion', '_Series_B'), ('6sense', '_Series_A'), ('8Securities', '_Series_A'), ('AHAlife', '_Series_B'), ('AbilTo', '_Series_A'), ('AbilTo', '_Series_B'), ('Abiquo', '_Series_A'), ('Achievers', '_Series_A'), ('Achievers', '_Series_C'), ('ActOnSoftware', '_Series_B'), ('ActOnSoftware', '_Series_C'), ('ActOnSoftware', '_Series_D'), ('ActonSoftware', '_Series_B'), ('ActonSoftware', '_Series_C'), ('ActonSoftware', '_Series_D'), ('Acumatica', '_Series_C'), ('AdMeld', '_Series_C'), ('AdReady', '_Series_C'), ('AdScale', '_Series_B'), ('Adaptiveblue', '_Series_B'), ('Adaptivity', '_Series_B'), ('Addepar', '_Series_B'), ('AdzCentral', '_Series_A'), ('AdzCentral', '_Series_B'), ('Aereo', '_Series_A'), ('Aereo', '_Series_B'), ('Aereo', '_Series_C'), ('Affectiva', '_Series_B'), ('Aipai', '_Series_C'), ('Airware', '_Series_B'), ('Alfresco', '

In [29]:
# We are now incorporate the translated tweets that Roger generated
valid_tweets_pd = pd.concat(valid_tweets)# If the tweet is not in the list of valid tweets, we don't want to include it
for row in tweets_translated.iterrows():
    company = row[1]['Company']
    href = row[1]['Href']
    time = row[1]['Time']

    match_comp = valid_tweets_pd[valid_tweets_pd['Company'] == company]
    match_href = match_comp[match_comp['Href'] == href]
    match_time = match_href[match_href['Time'] == time]
    
    res = list(match_time.index)
    if len(res) == 1:
        index = res[0]
        valid_tweets_pd.set_value(index, 'Text', row[1].Text)

In [30]:
valid_tweets_pd.to_csv("valid_tweets.csv", encoding='utf-8')

In [31]:
len(tweets_translated)

198201

In [32]:
valid_tweets_pd = pd.concat(valid_tweets)
valid_tweets_pd['Likes'] = valid_tweets_pd.apply(lambda row: int(row['Likes'][0]), axis=1)
valid_tweets_pd['Retweets'] = valid_tweets_pd.apply(lambda row: int(row['Retweets'][0]), axis=1)

In [37]:
# Calculate average tweets
days = valid_tweets_pd.groupby(['Company', 'Series'])['Date_Num'].max() - valid_tweets_pd.groupby(['Company', 'Series'])['Date_Num'].min()
tweets = valid_tweets_pd.groupby(['Company', 'Series']).size()
avg_tweets = tweets / days

# Calculate total likes
total_likes= valid_tweets_pd.groupby(['Company', 'Series'])['Likes'].sum()

# Calculate total retweets
total_retweets = valid_tweets_pd.groupby(['Company', 'Series'])['Retweets'].sum()
companies = [val[0] for val in list(tweets.index)]
series = [val[1] for val in list(tweets.index)]

# Calculate all features
tweet_features = pd.DataFrame({'Index': range(1, 1+len(days)), 'Company':companies, 'Series':series, 'Total_Likes': total_likes, 'Total_Retweets': total_retweets, 'Avg_Tweets': avg_tweets})
tweet_features.index = range(1, 1+len(days))

# Open old funding data
funding_df = pd.read_csv("funding_collapsed.csv")
funding_df = funding_df.drop(['Unnamed: 0'], 1)
funding_df.rename(columns={'Names':'Company', 'Series_Type':'Series'}, inplace=True)

funding_df.head(15)

C:\Users\MY PC\AppData\Local\Temp\ipykernel_5472\776693786.py:20: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  funding_df = funding_df.drop(['Unnamed: 0'], 1)


Company Series_Amount   Series_Date    Series
0           Visualead    $1,600,000  Aug 15, 2013  Series_A
1            filmloop    $5,600,000  Feb  1, 2005  Series_A
2         Mochi-Media    $4,000,000  Mar 12, 2008  Series_A
3    SkyRecon-Systems    $3,730,000  Sep 12, 2005  Series_A
4          Lumos-Labs    $3,100,000  Jun  3, 2008  Series_A
5              ROBLOX    $2,200,000  Aug 14, 2009  Series_A
6             SendHub    $3,000,000  Sep  6, 2013  Series_A
7   Health-Guru-Media      $250,000  Jan  1, 2007  Series_A
8           White-Sky    $5,000,000  Sep 26, 2006  Series_A
9        Forus-Health    $5,000,000  Apr 27, 2012  Series_A
10          UberMedia    $3,500,000  Apr 11, 2010  Series_A
11        Dailymotion    $9,500,000  Aug  1, 2006  Series_A
12         Pernixdata    $7,000,000  Jan  1, 2012  Series_A
13            Divante      $850,000  Mar  1, 2013  Series_A
14    Message-Systems    $6,000,000  Mar 25, 2010  Series_A

In [39]:
# Merge the tweet features with the funding data
regress_features = pd.merge(tweet_features, funding_df, how='right', on=['Company', 'Series'])
regress_features = regress_features.drop('Index', 1)
regress_features = regress_features[([type(amount) == str for amount in list(regress_features.Series_Amount)])]
regress_features['Series_Amount'] = regress_features.apply(lambda row: int(row['Series_Amount'][1:].replace(',','')), axis=1)
regress_features.to_csv("regress_features.csv")

C:\Users\MY PC\AppData\Local\Temp\ipykernel_5472\1828099666.py:3: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  regress_features = regress_features.drop('Index', 1)
